In [1]:
import pandas as pd
import numpy as np
import os
from datetime import datetime
import matplotlib.pyplot as pltb

In [2]:
pd.options.display.max_columns = None
pd.options.display.max_rows = 500
pd.set_option('max_colwidth',40)

### Load data frame

In [3]:
os.chdir(r'C:\Users\Sellit\Desktop\BA_Coding\Data\1final_out')

In [4]:
start4=datetime.now()

df= pd.read_hdf('DataFrame_3_df.h5', 'df')

end4 = datetime.now()
print(end4 - start4)

0:00:00.482745


### Prepare X and y

In [60]:
y = df['purchase']
X = df.drop('purchase', axis=1)

### Logistic Regression

In [61]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, confusion_matrix

In [204]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state=24)

In [205]:
X_train.corr()

dist_on_page_cat1  \
dist_on_page_cat1                                  1.000000   
dist_on_page_cat2                                  0.119705   
dist_on_page_cat3                                 -0.008082   
dist_on_page_home                                  0.108713   
dist_on_page_info                                 -0.008741   
dist_on_page_marken                                0.016711   
dist_on_page_product                               0.001735   
dist_on_page_search                               -0.007429   
entry_page_cat_account                            -0.008531   
entry_page_cat_cat1                                0.229952   
entry_page_cat_cat2                               -0.083435   
entry_page_cat_cat3                               -0.056819   
entry_page_cat_home                                0.094607   
entry_page_cat_info                                0.006223   
entry_page_cat_marken                              0.061673   
entry_page_cat_product                            -0.009026   
entry_page_cat_search                             -0.014145   
max_y_cat1                                         0.862605   
max_y_cat2                                         0.099757   
max_y_cat3                                        -0.042872   
max_y_home                                         0.073828   
max_y_info                                        -0.008584   
max_y_marken                                       0.011564   
max_y_product                                     -0.016788   
max_y_search                                      -0.025726   
mean_velocity_cat1                                 0.766304   
mean_velocity_cat2                                 0.084923   
mean_velocity_cat3                                -0.050149   
mean_velocity_home                                 0.142350   
mean_velocity_info                                -0.009791   
mean_velocity_marken                               0.018224   
mean_velocity_product                             -0.008878   
mean_velocity_search                              -0.000442   
page_cat_account_y                                 0.010130   
page_cat_cat1_y                                    0.598278   
page_cat_cat2_y                                    0.009120   
page_cat_cat3_y                                   -0.085519   
page_cat_home_y                                    0.087713   
page_cat_info_y                                   -0.006424   
page_cat_marken_y                                  0.016364   
page_cat_notes_y                                  -0.006940   
page_cat_product_y                                -0.093316   
page_cat_search_y                                 -0.028058   
referrerType_                                      0.018770   
referrerType_Link                                 -0.012270   
referrerType_Search                               -0.009168   
ta_area_map_Ad                                    -0.021319   
ta_area_map_Ad_time_on_oject_aggregated           -0.026294   
ta_area_map_Advisor                               -0.040485   
ta_area_map_Advisor_time_on_oject_agg...          -0.032234   
ta_area_map_AehnlicheArtikel/ZubehörT...          -0.031878   
ta_area_map_AehnlicheArtikel/ZubehörT...          -0.022412   
ta_area_map_AreaCalculation                       -0.000056   
ta_area_map_AreaCalculation_time_on_o...           0.015551   
ta_area_map_ContactMenu                           -0.010489   
ta_area_map_ContactMenu_time_on_oject...           0.004741   
ta_area_map_Filter                                 0.001395   
ta_area_map_Filter_time_on_oject_aggr...          -0.019095   
ta_area_map_Footer                                -0.006197   
ta_area_map_Footer_time_on_oject_aggr...          -0.008227   
ta_area_map_Header                                -0.019238   
ta_area_map_Header_time_on_oject_aggr...          -0.004571   
ta_area_map_In den Warenkorb                      -0.015975   
ta_area_ma

#### All columns

In [206]:
from sklearn import linear_model
import numpy as np
import scipy.stats as stat

class LogisticReg:
    """
    Wrapper Class for Logistic Regression which has the usual sklearn instance 
    in an attribute self.model, and pvalues, z scores and estimated 
    errors for each coefficient in 
    
    self.z_scores
    self.p_values
    self.sigma_estimates
    
    as well as the negative hessian of the log Likelihood (Fisher information)
    
    self.F_ij
    """
    
    def __init__(self,*args,**kwargs):#,**kwargs):
        self.model = linear_model.LogisticRegression(*args,**kwargs)#,**args)

    def fit(self,X,y):
        self.model.fit(X,y)
        #### Get p-values for the fitted model ####
        denom = (2.0*(1.0+np.cosh(self.model.decision_function(X))))
        denom = np.tile(denom,(X.shape[1],1)).T
        F_ij = np.dot((X/denom).T,X) ## Fisher Information Matrix
        Cramer_Rao = np.linalg.inv(F_ij) ## Inverse Information Matrix
        sigma_estimates = np.array([np.sqrt(Cramer_Rao[i,i]) for i in range(Cramer_Rao.shape[0])]) # sigma for each coefficient
        z_scores = self.model.coef_[0]/sigma_estimates # z-score for eaach model coefficient
        p_values = [stat.norm.sf(abs(x))*2 for x in z_scores] ### two tailed test for p-values
        
        self.z_scores = z_scores
        self.p_values = p_values
        self.sigma_estimates = sigma_estimates
        self.F_ij = F_ij

### Without weights

In [207]:
logreg = LogisticReg()

In [208]:
logreg.fit(X_train, y_train)

#### Test data set

In [209]:
y_pred = logreg.model.predict(X_test)

In [210]:
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[1959   40]
 [ 358   85]]
             precision    recall  f1-score   support

      False       0.85      0.98      0.91      1999
       True       0.68      0.19      0.30       443

avg / total       0.82      0.84      0.80      2442



In [211]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_test)]
auc = roc_auc_score(y_test, y_hat)

print(auc)

0.6932653685759358


In [212]:
logreg.model.score(X_test, y_test)

0.8370188370188371

In [213]:
p = logreg.p_values

In [214]:
weights = np.std(X)*logreg.model.coef_[0]

In [215]:
col = (X_train.columns)

In [216]:
pd.DataFrame({'Feature':col,'weights':weights, 'p-value':p}).sort_values(by=['weights'], ascending = False)

Feature  \
time_no_movement_info                                       time_no_movement_info   
time_no_movement_cat1                                       time_no_movement_cat1   
time_no_movement_product                                 time_no_movement_product   
ta_area_map_In den Warenkorb_time_on_...  ta_area_map_In den Warenkorb_time_on...   
time_no_movement_cat3                                       time_no_movement_cat3   
dist_on_page_home                                               dist_on_page_home   
time_no_movement_search                                   time_no_movement_search   
time_no_movement_cat2                                       time_no_movement_cat2   
ta_area_map_AreaCalculation_time_on_o...  ta_area_map_AreaCalculation_time_on_...   
ta_area_map_Quantity_time_on_oject_ag...  ta_area_map_Quantity_time_on_oject_a...   
ta_area_map_Picture_main_time_on_ojec...  ta_area_map_Picture_main_time_on_oje...   
ta_area_map_Header_time_on_oject_aggr...  ta_area_map_Header_time_on_oject_agg...   
ta_area_map_ProductHeader_time_on_oje...  ta_area_map_ProductHeader_time_on_oj...   
ta_area_map_Zubehör_time_on_oject_agg...  ta_area_map_Zubehör_time_on_oject_ag...   
ta_area_map_Last viewed_time_on_oject...  ta_area_map_Last viewed_time_on_ojec...   
max_y_home                                                             max_y_home   
ta_area_map_ProductDescription_time_o...  ta_area_map_ProductDescription_time_...   
ta_area_map_Footer_time_on_oject_aggr...  ta_area_map_Footer_time_on_oject_agg...   
visitTime_home                                                     visitTime_home   
mean_velocity_home                                             mean_velocity_home   
ta_area_map_ContactMenu_time_on_oject...  ta_area_map_ContactMenu_time_on_ojec...   
page_cat_home_y                                                   page_cat_home_y   
entry_page_cat_home                                           entry_page_cat_home   
page_cat_account_y                                             page_cat_account_y   
ta_area_map_In den Warenkorb                         ta_area_map_In den Warenkorb   
ta_area_map_AreaCalculation                           ta_area_map_AreaCalculation   
ta_area_map_Quantity                                         ta_area_map_Quantity   
ta_area_map_ContactMenu                                   ta_area_map_ContactMenu   
page_cat_notes_y                                                 page_cat_notes_y   
entry_page_cat_cat1                                           entry_page_cat_cat1   
entry_page_cat_account                                     entry_page_cat_account   
entry_page_cat_search                                       entry_page_cat_search   
entry_page_cat_marken                                       entry_page_cat_marken   
entry_page_cat_info                                           entry_page_cat_info   
referrerType_Link                                               referrerType_Link   
page_cat_cat1_y                                                   page_cat_cat1_y   
ta_area_map_Topbar                                             ta_area_map_Topbar   
page_cat_marken_y                                               page_cat_marken_y   
ta_area_map_Title                                               ta_area_map_Title   
ta_area_map_Last viewed                                   ta_area_map_Last viewed   
ta_area_map_ProductHeader                               ta_area_map_ProductHeader   
ta_area_map_Search                                             ta_area_map_Search   
page_cat_info_y                                                   page_cat_info_y   
ta_area_map_Ad                                                     ta_area_map_Ad   
ta_area_map_ZuletztAngesehen                         ta_area_map_ZuletztAngesehen   
ta_area_map_Footer                                             ta_area_map_Footer   
ta_area_map_ZudenSortimenten                         ta_area_map_ZudenSortiment

#### Training data set

In [217]:
y_pred = logreg.model.predict(X_train)

In [218]:
print(confusion_matrix(y_train, y_pred))
print(classification_report(y_train, y_pred))

[[4608   99]
 [ 824  166]]
             precision    recall  f1-score   support

      False       0.85      0.98      0.91      4707
       True       0.63      0.17      0.26       990

avg / total       0.81      0.84      0.80      5697



In [219]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_train)]
auc = roc_auc_score(y_train, y_hat)

print(auc)

0.7128268021193452


In [220]:
logreg.model.score(X_train, y_train)

0.8379849043356152

### With weights

In [221]:
logreg = LogisticReg(class_weight = {1:.75, 0:.25})

In [222]:
logreg.fit(X_train, y_train)

#### Test data set

In [223]:
y_pred = logreg.model.predict(X_test)

In [224]:
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[1762  237]
 [ 226  217]]
             precision    recall  f1-score   support

      False       0.89      0.88      0.88      1999
       True       0.48      0.49      0.48       443

avg / total       0.81      0.81      0.81      2442



In [225]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_test)]
auc = roc_auc_score(y_test, y_hat)

print(auc)

0.7473544898860266


In [226]:
logreg.model.score(X_test, y_test)

0.8104013104013104

In [227]:
p = logreg.p_values

In [228]:
weights = np.std(X)*logreg.model.coef_[0]

In [229]:
col = (X_train.columns)

In [230]:
feature_coef = pd.DataFrame({'Feature':col,'weights':weights, 'p-value':p}).sort_values(by=['weights'], ascending = False)

In [231]:
feature_coef

Feature  \
ta_area_map_In den Warenkorb_time_on_...  ta_area_map_In den Warenkorb_time_on...   
time_no_movement_cat1                                       time_no_movement_cat1   
time_no_movement_info                                       time_no_movement_info   
time_no_movement_product                                 time_no_movement_product   
mean_velocity_home                                             mean_velocity_home   
time_no_movement_cat3                                       time_no_movement_cat3   
visitTime_home                                                     visitTime_home   
ta_area_map_Picture_main_time_on_ojec...  ta_area_map_Picture_main_time_on_oje...   
dist_on_page_home                                               dist_on_page_home   
dist_on_page_marken                                           dist_on_page_marken   
time_no_movement_cat2                                       time_no_movement_cat2   
time_no_movement_search                                   time_no_movement_search   
mean_velocity_cat1                                             mean_velocity_cat1   
ta_area_map_Header_time_on_oject_aggr...  ta_area_map_Header_time_on_oject_agg...   
max_y_info                                                             max_y_info   
ta_area_map_AreaCalculation_time_on_o...  ta_area_map_AreaCalculation_time_on_...   
dist_on_page_cat3                                               dist_on_page_cat3   
mean_velocity_search                                         mean_velocity_search   
dist_on_page_cat2                                               dist_on_page_cat2   
ta_area_map_Last viewed_time_on_oject...  ta_area_map_Last viewed_time_on_ojec...   
ta_area_map_ProductHeader_time_on_oje...  ta_area_map_ProductHeader_time_on_oj...   
ta_area_map_Zubehör_time_on_oject_agg...  ta_area_map_Zubehör_time_on_oject_ag...   
ta_area_map_Search_time_on_oject_aggr...  ta_area_map_Search_time_on_oject_agg...   
max_y_home                                                             max_y_home   
dist_on_page_product                                         dist_on_page_product   
page_cat_home_y                                                   page_cat_home_y   
entry_page_cat_home                                           entry_page_cat_home   
ta_area_map_ProductHeader                               ta_area_map_ProductHeader   
page_cat_account_y                                             page_cat_account_y   
ta_area_map_In den Warenkorb                         ta_area_map_In den Warenkorb   
ta_area_map_Quantity                                         ta_area_map_Quantity   
referrerType_Link                                               referrerType_Link   
ta_area_map_Picture_main                                 ta_area_map_Picture_main   
referrerType_                                                       referrerType_   
ta_area_map_ContactMenu                                   ta_area_map_ContactMenu   
page_cat_cat1_y                                                   page_cat_cat1_y   
page_cat_notes_y                                                 page_cat_notes_y   
entry_page_cat_cat1                                           entry_page_cat_cat1   
ta_area_map_AreaCalculation                           ta_area_map_AreaCalculation   
entry_page_cat_search                                       entry_page_cat_search   
ta_area_map_Topbar                                             ta_area_map_Topbar   
ta_area_map_ProductDetails_Right                 ta_area_map_ProductDetails_Right   
entry_page_cat_account                                     entry_page_cat_account   
ta_area_map_Pagination                                     ta_area_map_Pagination   
entry_page_cat_marken                                       entry_page_cat_marken   
entry_page_cat_info                                           entry_page_cat_info   
page_cat_search_y                                               page_cat_search

In [233]:
os.chdir(r'C:\Users\Sellit\Desktop\BA_Coding\Data\1final_out') 
writer = pd.ExcelWriter('feature_coef.xlsx') 
feature_coef.to_excel(writer,'Sheet1')

#### Training data set

In [234]:
y_pred = logreg.model.predict(X_train)

In [235]:
print(confusion_matrix(y_train, y_pred))
print(classification_report(y_train, y_pred))

[[4177  530]
 [ 535  455]]
             precision    recall  f1-score   support

      False       0.89      0.89      0.89      4707
       True       0.46      0.46      0.46       990

avg / total       0.81      0.81      0.81      5697



In [236]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_train)]
auc = roc_auc_score(y_train, y_hat)

print(auc)

0.7686327906213184


In [237]:
logreg.model.score(X_train, y_train)

0.8130595050026329

### Comparison between mouse movement variables and page level information

### Mouse movement

In [238]:
col_cat1 = 'ta_area_map'
col_cat2 = 'time_no_movement'
col_cat3 = 'mean_velocity'
col_cat4 = 'dist_on_page'
col_cat5 = 'max_y'
col_cat6 = 'purchase'

list_col1 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat1)])
list_col2 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat2)])
list_col3 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat3)])
list_col4 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat4)])
list_col5 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat5)])
list_col6 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat6)])
list_col1.extend(list_col2)
list_col1.extend(list_col3)
list_col1.extend(list_col4)
list_col1.extend(list_col5)
list_col1.extend(list_col6)

df_mouse_movement = df[list_col1]

In [239]:
df_mouse_movement

ta_area_map_Ad  ta_area_map_Ad_time_on_oject_aggregated  \
0                  0                                        0   
1                  0                                        0   
2                  1                                        0   
3                  0                                        0   
6                  0                                        0   
7                  0                                        0   
8                  0                                        0   
13                 0                                        0   
14                 0                                        0   
16                 0                                        0   
17                 0                                        0   
18                 0                                        0   
26                 0                                        0   
28                 0                                        0   
29                 0                                        0   
31                 0                                        0   
32                 0                                        0   
33                 0                                        0   
34                 0                                        0   
35                 0                                        0   
36                 0                                        0   
37                 0                                        0   
38                 0                                        0   
43                 0                                        0   
47                 0                                        0   
48                 1                                        0   
50                 0                                        0   
52                 0                                        0   
53                 0                                        0   
54                 0                                        0   
57                 0                                        0   
59                 0                                        0   
60                 0                                        0   
62                 0                                        0   
63                 0                                        0   
64                 0                                        0   
68                 0                                        0   
69                 0                                        0   
70                 0                                        0   
72                 0                                        0   
73                 0                                        0   
74                 0                                        0   
75                 0                                        0   
76                 0                                        0   
77                 0                                        0   
78                 1                                        0   
83                 0                                        0   
84                 0                                        0   
87                 0                                        0   
89                 0                                        0   
90                 0                                        0   
91                 0                                        0   
92                 0                                        0   
95                 0                                        0   
98                 0                                        0   
99                 0                                        0   
100                0                                        0   
102                0                                        0   
106                0                                        0   
109                0                                        0   
110                0                     

In [240]:
y = df_mouse_movement['purchase']
X = df_mouse_movement.drop('purchase', axis=1)

In [241]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state=24)

In [242]:
logreg = LogisticReg(class_weight = {1:.75, 0:.25})

In [243]:
logreg.fit(X_train, y_train)

#### Test data set

In [244]:
y_pred = logreg.model.predict(X_test)

In [245]:
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[1754  245]
 [ 228  215]]
             precision    recall  f1-score   support

      False       0.88      0.88      0.88      1999
       True       0.47      0.49      0.48       443

avg / total       0.81      0.81      0.81      2442



In [246]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_test)]
auc = roc_auc_score(y_test, y_hat)

print(auc)

0.7507839698630353


In [247]:
logreg.model.score(X_test, y_test)

0.8063063063063063

In [248]:
p = logreg.p_values

In [249]:
weights = np.std(X)*logreg.model.coef_[0]

In [250]:
col = (X_train.columns)

In [251]:
pd.DataFrame({'Feature':col,'weights':weights, 'p-value':p}).sort_values(by=['weights'], ascending = False)

Feature  \
ta_area_map_In den Warenkorb_time_on_...  ta_area_map_In den Warenkorb_time_on...   
mean_velocity_home                                             mean_velocity_home   
time_no_movement_product                                 time_no_movement_product   
time_no_movement_cat1                                       time_no_movement_cat1   
ta_area_map_Picture_main_time_on_ojec...  ta_area_map_Picture_main_time_on_oje...   
dist_on_page_home                                               dist_on_page_home   
dist_on_page_marken                                           dist_on_page_marken   
ta_area_map_Header_time_on_oject_aggr...  ta_area_map_Header_time_on_oject_agg...   
ta_area_map_AreaCalculation_time_on_o...  ta_area_map_AreaCalculation_time_on_...   
time_no_movement_cat3                                       time_no_movement_cat3   
dist_on_page_cat3                                               dist_on_page_cat3   
ta_area_map_Last viewed_time_on_oject...  ta_area_map_Last viewed_time_on_ojec...   
mean_velocity_search                                         mean_velocity_search   
mean_velocity_cat1                                             mean_velocity_cat1   
time_no_movement_search                                   time_no_movement_search   
time_no_movement_cat2                                       time_no_movement_cat2   
dist_on_page_cat2                                               dist_on_page_cat2   
ta_area_map_Zubehör_time_on_oject_agg...  ta_area_map_Zubehör_time_on_oject_ag...   
max_y_info                                                             max_y_info   
ta_area_map_ProductHeader_time_on_oje...  ta_area_map_ProductHeader_time_on_oj...   
ta_area_map_Search_time_on_oject_aggr...  ta_area_map_Search_time_on_oject_agg...   
time_no_movement_info                                       time_no_movement_info   
max_y_home                                                             max_y_home   
ta_area_map_ProductHeader                               ta_area_map_ProductHeader   
ta_area_map_In den Warenkorb                         ta_area_map_In den Warenkorb   
ta_area_map_Quantity                                         ta_area_map_Quantity   
ta_area_map_Picture_main                                 ta_area_map_Picture_main   
ta_area_map_ContactMenu                                   ta_area_map_ContactMenu   
ta_area_map_AreaCalculation                           ta_area_map_AreaCalculation   
ta_area_map_Pagination                                     ta_area_map_Pagination   
ta_area_map_Topbar                                             ta_area_map_Topbar   
ta_area_map_ZuletztAngesehen                         ta_area_map_ZuletztAngesehen   
ta_area_map_ZudenSortimenten                         ta_area_map_ZudenSortimenten   
ta_area_map_Footer                                             ta_area_map_Footer   
ta_area_map_Search                                             ta_area_map_Search   
ta_area_map_ProductDetails_Right                 ta_area_map_ProductDetails_Right   
ta_area_map_Last viewed                                   ta_area_map_Last viewed   
ta_area_map_Title                                               ta_area_map_Title   
ta_area_map_Products                                         ta_area_map_Products   
ta_area_map_Ad                                                     ta_area_map_Ad   
ta_area_map_Zubehör                                           ta_area_map_Zubehör   
ta_area_map_Header                                             ta_area_map_Header   
ta_area_map_AehnlicheArtikel/ZubehörT...  ta_area_map_AehnlicheArtikel/Zubehör...   
ta_area_map_Navigation                                     ta_area_map_Navigation   
ta_area_map_Sidebar                                           ta_area_map_Sidebar   
ta_area_map_ProductDescription                     ta_area_map_ProductDescription   
ta_area_map_Filter                                             ta_area_map_Filt

#### Training data set

In [252]:
y_pred = logreg.model.predict(X_train)

In [253]:
print(confusion_matrix(y_train, y_pred))
print(classification_report(y_train, y_pred))

[[4170  537]
 [ 540  450]]
             precision    recall  f1-score   support

      False       0.89      0.89      0.89      4707
       True       0.46      0.45      0.46       990

avg / total       0.81      0.81      0.81      5697



In [254]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_train)]
auc = roc_auc_score(y_train, y_hat)

print(auc)

0.7629485850645825


In [255]:
logreg.model.score(X_train, y_train)

0.8109531332280148

### Page level information

In [256]:
col_cat1 = 'page_cat'
col_cat2 = 'entry_page_cat'
col_cat3 = 'referrerType'
col_cat4 = 'visitTime'
col_cat5 = 'purchase'

list_col1 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat1)])
list_col2 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat2)])
list_col3 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat3)])
list_col4 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat4)])
list_col5 = list(df.columns[pd.Series(df.columns).str.startswith(col_cat5)])

list_col1.extend(list_col2)
list_col1.extend(list_col3)
list_col1.extend(list_col4)
list_col1.extend(list_col5)

df_page_level = df[list_col1]

In [257]:
df_page_level

page_cat_account_y  page_cat_cat1_y  page_cat_cat2_y  page_cat_cat3_y  \
0                      4                0                0                0   
1                      0                0                0                0   
2                      0                0                1                1   
3                      3                0                0                0   
6                      0                1                2                0   
7                      0                1                2                1   
8                      0                1                2                0   
13                     0                1                2                0   
14                     0                0                0                0   
16                     0                0                1                3   
17                     0                0                1                3   
18                     0                1                2                1   
26                     0                0                0                2   
28                     0                0                0                0   
29                     0                2                1                0   
31                     0                0                1                0   
32                     0                0                2                3   
33                     0                0                2                2   
34                     0                0                5                0   
35                     0                0                2                0   
36                     0                0                0                0   
37                     3                0                1                0   
38                     0                0                0                1   
43                     0                0                1                1   
47                     0                0                2                0   
48                     0                0                4                0   
50                     4                0                0                0   
52                     0                0                0                0   
53                     0                0                0                0   
54                     0                0                4                0   
57                     0                1                1                0   
59                     0                0                0                3   
60                     0                0                2                2   
62                     0                0                3                0   
63                     0                0                2                0   
64                     0                0                0                0   
68                     0                1                2                0   
69                     0                0                1                2   
70                     0                0                3                0   
72                     0                1                2                0   
73                     0                0                0                0   
74                     0                0                0                4   
75                     0                0                1                3   
76                     0                0                3                1   
77                     0                0                0                4   
78                     0                0                2                0   
83                     0                0                0                0   
84                     0                0                0                1   
87                     0                0                0                0   
89                     0                0               

In [258]:
y = df_page_level['purchase']
X = df_page_level.drop('purchase', axis=1)

In [259]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state=24)

In [260]:
logreg = LogisticReg(class_weight = {1:.75, 0:.25})

In [261]:
logreg.fit(X_train, y_train)

#### Test data set

In [262]:
y_pred = logreg.model.predict(X_test)

In [263]:
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test, y_pred))

[[1962   37]
 [ 408   35]]
             precision    recall  f1-score   support

      False       0.83      0.98      0.90      1999
       True       0.49      0.08      0.14       443

avg / total       0.77      0.82      0.76      2442



In [264]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_test)]
auc = roc_auc_score(y_test, y_hat)

print(auc)

0.6906094130586738


In [265]:
logreg.model.score(X_test, y_test)

0.8177723177723177

In [266]:
p = logreg.p_values

In [267]:
weights = np.std(X)*logreg.model.coef_[0]

In [268]:
col = (X_train.columns)

In [269]:
pd.DataFrame({'Feature':col,'weights':weights, 'p-value':p}).sort_values(by=['weights'], ascending = False)

Feature   weights   p-value
visitTime_home                  visitTime_home  0.171000  0.005926
visitTime_product            visitTime_product  0.116678  0.000731
visitTime_cat1                  visitTime_cat1  0.030648  0.376595
page_cat_home_y                page_cat_home_y  0.017650  0.795010
visitTime_search              visitTime_search  0.014679  0.593683
entry_page_cat_home        entry_page_cat_home  0.013456  0.960965
page_cat_account_y          page_cat_account_y  0.009506  0.818610
visitTime_cat3                  visitTime_cat3  0.003370  0.902023
visitTime_info                  visitTime_info  0.003094  0.913529
page_cat_notes_y              page_cat_notes_y  0.000355  0.989912
page_cat_cat1_y                page_cat_cat1_y  0.000265  0.994727
entry_page_cat_cat1        entry_page_cat_cat1  0.000140  0.998737
entry_page_cat_account  entry_page_cat_account  0.000068  0.998901
entry_page_cat_search    entry_page_cat_search -0.000008  0.999911
entry_page_cat_marken    entry_page_cat_marken -0.000087  0.999156
entry_page_cat_info        entry_page_cat_info -0.000144  0.998489
referrerType_Link            referrerType_Link -0.000813  0.997582
page_cat_marken_y            page_cat_marken_y -0.001651  0.969053
page_cat_info_y                page_cat_info_y -0.002269  0.956926
referrerType_                    referrerType_ -0.005082  0.988903
entry_page_cat_cat3        entry_page_cat_cat3 -0.007945  0.976559
page_cat_search_y            page_cat_search_y -0.009692  0.877076
entry_page_cat_product  entry_page_cat_product -0.013353  0.970405
visitTime_cat2                  visitTime_cat2 -0.018729  0.506640
entry_page_cat_cat2        entry_page_cat_cat2 -0.025860  0.942065
referrerType_Search        referrerType_Search -0.027335  0.943767
page_cat_product_y          page_cat_product_y -0.096107  0.367259
page_cat_cat3_y                page_cat_cat3_y -0.176007  0.125266
visitTime_marken              visitTime_marken -0.238160  0.054813
page_cat_cat2_y                page_cat_cat2_y -0.292148  0.020238

#### Training data set

In [73]:
y_pred = logreg.model.predict(X_train)

In [74]:
print(confusion_matrix(y_train, y_pred))
print(classification_report(y_train, y_pred))

[[4632   75]
 [ 926   64]]
             precision    recall  f1-score   support

      False       0.83      0.98      0.90      4707
       True       0.46      0.06      0.11       990

avg / total       0.77      0.82      0.77      5697



In [75]:
from sklearn.metrics import roc_auc_score

y_hat = [x[1] for x in logreg.model.predict_proba(X_train)]
auc = roc_auc_score(y_train, y_hat)

print(auc)

0.6745783734948808


In [76]:
logreg.model.score(X_train, y_train)

0.8242934878005969